In [1]:
import pandas as pd
import pymysql
import re
import random
import urllib
import requests

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all" 

# 数据合并

In [2]:
conn = pymysql.connect( 
    host="localhost",
    user="root",
    password="YUAN69188059*", 
    database="douban",
    charset="utf8"
)

cursor = conn.cursor()
#打开数据库中的文件
books = pd.read_sql('select * from books',conn)
books.head(10)
books_top250 = pd.read_sql('select * from books_top250',conn)
books_top250.head(10)
#打开工作室提供的书籍数据，删掉第一行，并添加索引
QGbooks = pd.read_csv(r'douban_book_release.txt', delimiter="\t", names = ["BOOK_NAME","AUTHOR","PRESS","PUBLISHING_YEAR","SCORE","RATING_NUM","PAGE_NUM","PRICE","ISBN","CONTENT_INTRODUCTION","COVER_URL","READERS"])
QGbooks = QGbooks.drop([0],axis = 0)
QGbooks.head(10)

BOOK_NAME          AUTHOR      PRESS PUBLISHING_YEAR SCORE RATING_NUM  \
0        活着              余华      作家出版社            2012   9.4     588677   
1        文城              余华  北京十月文艺出版社            2021   7.8      11350   
2       白夜行         [日]东野圭吾     南海出版公司            2013   9.1     338400   
3       红楼梦     [清]曹雪芹著、高鹗续    人民文学出版社            1996   9.6     331381   
4     暗夜与黎明        [英]肯·福莱特  江苏凤凰文艺出版社            2021   8.1       2202   
5    克拉拉与太阳         [英]石黑一雄    上海译文出版社            2021   8.4       5299   
6  房思琪的初恋乐园             林奕含   北京联合出版公司            2018   9.2     243784   
7       小王子       [法]圣埃克苏佩里    人民文学出版社            2003   9.0     632532   
8      百年孤独  [哥伦比亚]加西亚·马尔克斯     南海出版公司            2011   9.3     331924   
9     追风筝的人      [美]卡勒德·胡赛尼    上海人民出版社            2006   8.9     691306   

  PAGE_NUM    PRICE           ISBN  \
0      191   20.00元  9787506365437   
1      348   59.00元  9787530221099   
2      538   39.50元  9787544258609   
3     1606   59.70元  9787020002207   
4      960  118.00元  9787559454935   
5      392    68.00  9787532786831   
6      272   45.00元  9787559614636   
7       97   22.00元  9787020042494   
8      360   39.50元  9787544253994   
9      362   29.00元  9787208061644   

                                CONTENT_INTRODUCTION  \
0  《活着(新版)》讲述了农村人福贵悲惨的人生遭遇。福贵本是个阔少爷，可他嗜赌如命，终于赌光了家...   
1  【编辑推荐】★时隔八年，余华全新长篇重磅归来！◆人生就是自己的往事和他人的序章时代的洪流推着...   
2  东野圭吾万千书迷心中的无冕之王周刊文春推理小说年度BEST10第1名本格推理小说年度BEST...   
3  《红楼梦》是一部百科全书式的长篇小说。以宝黛爱情悲剧为主线，以四大家族的荣辱兴衰为背景，描绘...   
4  《巨人的陨落》作者肯•福莱特重磅新作！全球读者平均2个通宵读完！--------------...   
5  “太阳总有办法照到我们，不管我们在哪里。”~克拉拉是一个专为陪伴儿童而设计的太阳能人工智能机...   
6  令人心碎却无能为力的真实故事。向死而生的文学绝唱  打动万千读者的年度华语小说。李银河 戴锦...   
7  小王子是一个超凡脱俗的仙童，他住在一颗只比他大一丁点儿的小行星上。陪伴他的是一朵他非常喜爱的...   
8  《百年孤独》是魔幻现实主义文学的代表作，描写了布恩迪亚家族七代人的传奇故事，以及加勒比海沿岸...   
9  12岁的阿富汗富家少爷阿米尔与仆人哈桑情同手足。然而，在一场风筝比赛后，发生了一件悲惨不堪的...   

                                           COVER_URL  \
0  https://img3.doubanio.com/view/subject/s/publi...   
1  https://img1.doubanio.com/view/subject/s/publi...   
2  https://img1.doubanio.com/view/subject/s/publi...   
3  https://img1.doubanio.com/view/subject/s/publi...   
4  https://img2.doubanio.com/view/subject/s/publi...   
5  https://img9.doubanio.com/view/subject/s/publi...   
6  https://img3.doubanio.com/view/subject/s/publi...   
7  https://img2.doubanio.com/view/subject/s/publi...   
8  https://img3.doubanio.com/view/subject/s/publi...   
9  https://img3.doubanio.com/view/subject/s/publi...   

                                             READERS  
0  https://www.douban.com/people/scorpio0_0/https...  
1  https://www.douban.com/people/zcj1568/https://...  
2  https://www.douban.com/people/amber_xyxy/https...  
3  https://www.douban.com/people/lostgarden/https...  
4  https://www.douban.com/people/ourdookbook/http...  
5  https://www.douban.com/people/1747760/https://...  
6  https://www.douban.com/people/160664420/https:...  
7  https://www.douban.com/people/helizhanglao/htt...  
8  https://www.douban.com/people/xiacat/https://w...  
9  https://www.douban.com/people/1182787/https://...

BOOK_NAME           AUTHOR      PRESS PUBLISHING_YEAR  SCORE RATING_NUM  \
0        红楼梦        [清] 曹雪芹 著    人民文学出版社            1996   9.6      331377   
1         活着               余华      作家出版社            2012   9.4      588665   
2       1984       [英] 乔治·奥威尔  北京十月文艺出版社            2010   9.3      179456   
3       百年孤独  [哥伦比亚] 加西亚·马尔克斯     南海出版公司            2011   9.3      331918   
4          飘    [美国] 玛格丽特·米切尔      译林出版社            2000   9.3      176255   
5       三体全集              刘慈欣      重庆出版社            2012   9.4       89959   
6  三国演义（全二册）          [明] 罗贯中    人民文学出版社            1998   9.3      136094   
7   房思琪的初恋乐园              林奕含   北京联合出版公司            2018   9.2      243771   
8       动物农场       [英] 乔治·奥威尔    上海译文出版社            2007   9.2      110563   
9        白夜行         [日] 东野圭吾     南海出版公司            2013   9.1      338383   

  PAGE_NUM    PRICE           ISBN  \
0     1606   59.70元  9787020002207   
1      191   20.00元  9787506365437   
2      304    28.00  9787530210291   
3      360   39.50元  9787544253994   
4     1235   40.00元  9787806570920   
5     1285  168.00元  9787229042066   
6      990   39.50元  9787020008728   
7      272   45.00元  9787559614636   
8      119   10.00元  9787532741854   
9      538   39.50元  9787544258609   

                                CONTENT_INTRODUCTION  \
0  《红楼梦》是一部百科全书式的长篇小说。以宝黛爱情悲剧为主线，以四大家族的荣辱兴衰为背景，描绘...   
1  《活着(新版)》讲述了农村人福贵悲惨的人生遭遇。福贵本是个阔少爷，可他嗜赌如命，终于赌光了家...   
2  ★村上春树以《1Q84》向本书致敬★著名学者刘绍铭经典译本内地首次出版★62种文字风靡110...   
3  《百年孤独》是魔幻现实主义文学的代表作，描写了布恩迪亚家族七代人的传奇故事，以及加勒比海沿岸...   
4  小说中的故事发生在1861年美国南北战争前夕。生活在南方的少女郝思嘉从小深受南方文化传统的熏...   
5  三体三部曲 (《三体》《三体Ⅱ·黑暗森林》《三体Ⅲ·死神永生》) ，原名“地球往事三部曲”，...   
6  《三国演义》又名《三国志演义》、《三国志通俗演义》，是我国小说史上最著名最杰出的长篇章回体历...   
7  令人心碎却无能为力的真实故事。向死而生的文学绝唱  打动万千读者的年度华语小说。李银河 戴锦...   
8  《动物农场》是奥威尔最优秀的作品之一，是一则入木三分的反乌托的政治讽喻寓言。农场的一群动物成...   
9  东野圭吾万千书迷心中的无冕之王周刊文春推理小说年度BEST10第1名本格推理小说年度BEST...   

                                           COVER_URL  \
0  https://img1.doubanio.com/view/subject/s/publi...   
1  https://img3.doubanio.com/view/subject/s/publi...   
2  https://img1.doubanio.com/view/subject/s/publi...   
3  https://img3.doubanio.com/view/subject/s/publi...   
4  https://img1.doubanio.com/view/subject/s/publi...   
5  https://img9.doubanio.com/view/subject/s/publi...   
6  https://img2.doubanio.com/view/subject/s/publi...   
7  https://img3.doubanio.com/view/subject/s/publi...   
8  https://img3.doubanio.com/view/subject/s/publi...   
9  https://img1.doubanio.com/view/subject/s/publi...   

                                             READERS  
0  https://www.douban.com/people/1361959/https://...  
1  https://www.douban.com/people/GayScript/https:...  
2  https://www.douban.com/people/penglingzhao/htt...  
3  https://www.douban.com/people/er-mao/https://w...  
4  https://www.douban.com/people/Dora-Y/https://w...  
5  https://www.douban.com/people/lyych/https://ww...  
6  https://www.douban.com/people/auxt/https://www...  
7  https://www.douban.com/people/xiaofeng0225/htt...  
8  https://www.douban.com/people/74570845/https:/...  
9  https://www.douban.com/people/flowfirefly/http...

BOOK_NAME                AUTHOR    PRESS PUBLISHING_YEAR SCORE  \
1    “可以不用长大”世界经典故事集  奥斯卡·王尔德/希梅内斯/赫尔曼·黑塞/    天地出版社            2021   9.2   
2               “萨福”                 田晓菲编译      NaN            2019   8.2   
3            “醒”后吐真言                   杨庆春    商务印书馆            2013     0   
4             “黑”话水浒                  无斋主人  中国社会出版社            2005     8   
5   《借东西的小人》全系列（全5册）              [英]玛丽·诺顿    译林出版社            2018     9   
6          《大江大河》四部曲                    阿耐      NaN            2018   8.3   
7      《新周刊》2010年度佳作              《新周刊》杂志社    漓江出版社            2011   8.7   
8           【推しの子】 １            赤坂アカ/横槍メンゴ      集英社            2020   8.3   
9           1/13密室杀人                    鸡丁      NaN            2013   8.3   
10    10 count (第1集)              [日本]宝井理人       東立            2014   8.5   

   RATING_NUM PAGE_NUM    PRICE           ISBN  \
1          20     1383  220.00元  9787545559484   
2          99      321   42.00元  9787108065827   
3           0      332   43.00元  9787100099608   
4         344      292    25.00  9787508704203   
5          18     1298      280  9787544772655   
6        5651     2300   320.00  9787559620446   
7         605      344   32.00元  9787540749842   
8          63        0     693円  9784088916507   
9         202      308   40.00元  9781993030625   
10       1087        0   NT$130  9789863653158   

                                 CONTENT_INTRODUCTION  \
1   写尽人间温暖的世界故事，每一页都能给你勇气与力量。 本套书选自世界文豪的经典故事，分别是来自...   
2   在欧美文学传统里，如果荷马是父亲，那么萨福则是母亲，她残缺的遗诗，是文学史的一次偶然事故，部...   
3   《“醒”后吐真言》作为一本杂文集，其大多抨击社会不平现象，初读起来觉得兴趣不大，但细细读来，...   
4   水浒是一本黑社会小说，梁山是个黑社会组织。“替天行道”的玫瑰色彩只是为了掩盖好汉们的暴行，个...   
5   “借东西的小人”全系列是享誉世界的童书经典，本版全彩精装印制，翻译家任溶溶经典译本重磅加盟，...   
6   同名电视剧《大江大河2》正在热播！ 《大江大河》以罕见的恢弘格局，全面、细致、深入地展现了中...   
7   《<新周刊>2010年度佳作》:漓江版年选 一年一度的文学盛宴 源自十四年如一日的品质守护 ...   
8   地方都市で、産婦人科医として働くゴロー。芸能界とは無縁の日々。一方、彼の“推し”のアイドル・...   
9   门窗反锁的房间中上吊的女人；高空行驶的缆车内被斩首的男人；铁丝网封口的水井中漂浮的女尸；众目...   
10  身為社長秘書的城谷忠臣雖然有優秀的工作能力，但也有嚴重的潔癖。他每天都戴著手套，酒精從不離身...   

                                            COVER_URL  \
1   https://img9.doubanio.com/view/subject/l/publi...   
2   https://img9.doubanio.com/view/subject/l/publi...   
3   https://img9.doubanio.com/view/subject/l/publi...   
4   https://img9.doubanio.com/view/subject/l/publi...   
5   https://img9.doubanio.com/view/subject/l/publi...   
6   https://img9.doubanio.com/view/subject/l/publi...   
7   https://img9.doubanio.com/view/subject/l/publi...   
8   https://img9.doubanio.com/view/subject/l/publi...   
9   https://img9.doubanio.com/view/subject/l/publi...   
10  https://img9.doubanio.com/view/subject/l/publi...   

                                              READERS  
1   ['https://www.douban.com/people/187301793/', '...  
2   ['https://www.douban.com/people/182845567/', '...  
3                                                  []  
4   ['https://www.douban.com/people/mirror416/', '...  
5   ['https://www.douban.com/people/48448737/', 'h...  
6   ['https://www.douban.com/people/179994436/', '...  
7   ['https://www.douban.com/people/holofenghao/',...  
8   ['https://www.douban.com/people/ethnomanchu/',...  
9   ['https://www.douban.com/people/1517177/', 'ht...  
10  ['https://www.douban.com/people/ktysnow/', 'ht...

In [4]:
#将3个dataframe链接在一起
books = pd.concat([books,books_top250,QGbooks],axis = 0, ignore_index=True)
books

BOOK_NAME       AUTHOR      PRESS PUBLISHING_YEAR SCORE RATING_NUM  \
0           活着           余华      作家出版社            2012   9.4     588677   
1           文城           余华  北京十月文艺出版社            2021   7.8      11350   
2          白夜行      [日]东野圭吾     南海出版公司            2013   9.1     338400   
3          红楼梦  [清]曹雪芹著、高鹗续    人民文学出版社            1996   9.6     331381   
4        暗夜与黎明     [英]肯·福莱特  江苏凤凰文艺出版社            2021   8.1       2202   
...        ...          ...        ...             ...   ...        ...   
8126        龙猫       [日]宫崎骏   北京联合出版公司            2020   8.9        484   
8127      龙猫的家       [日]宫崎骏     南海出版公司            2021   8.4        181   
8128      龙王闹海          郑渊洁  湖南少年儿童出版社          1989.7   8.7        733   
8129       龙珠1          鸟山明  中国少年儿童出版社            2005   9.5       1033   
8130  龟岛：斯奈德诗集    [美]加里·斯奈德        NaN            2021   8.6         28   

     PAGE_NUM    PRICE           ISBN  \
0         191   20.00元  9787506365437   
1         348   59.00元  9787530221099   
2         538   39.50元  9787544258609   
3        1606   59.70元  9787020002207   
4         960  118.00元  9787559454935   
...       ...      ...            ...   
8126      112   68.00元  9787559644633   
8127       89   88.00元  9787544299107   
8128      158     2.25  9787535804235   
8129      175      6.9  9787500774860   
8130      192    49.00  9787559647252   

                                   CONTENT_INTRODUCTION  \
0     《活着(新版)》讲述了农村人福贵悲惨的人生遭遇。福贵本是个阔少爷，可他嗜赌如命，终于赌光了家...   
1     【编辑推荐】★时隔八年，余华全新长篇重磅归来！◆人生就是自己的往事和他人的序章时代的洪流推着...   
2     东野圭吾万千书迷心中的无冕之王周刊文春推理小说年度BEST10第1名本格推理小说年度BEST...   
3     《红楼梦》是一部百科全书式的长篇小说。以宝黛爱情悲剧为主线，以四大家族的荣辱兴衰为背景，描绘...   
4     《巨人的陨落》作者肯•福莱特重磅新作！全球读者平均2个通宵读完！--------------...   
...                                                 ...   
8126  编辑推荐 【宫崎骏代表作首次授权！官方唯一简体中文版全球首发。】 ★30年间影响数代人的殿堂...   
8127  ★★★ 宫崎骏亲撰图文随笔，中文简体首度授权出版。 · 一直以来，我们只能通过电影、访谈“侧...   
8128  《龙王闹海》是童话作家郑渊洁所著十二生肖系列童话，该书包括龙珠风波、复活的恐龙、争龙年等多部...   
8129  《龙珠(套装共42册)》是日本著名漫画家鸟山明的得意作品。相传，有七颗龙珠散落在世界的各个角...   
8130  【编辑推荐】 ※垮掉派代表、禅宗诗人、“达摩流浪者”原型斯奈德 ※普利策诗歌奖获奖作品 ※把...   

                                              COVER_URL  \
0     https://img3.doubanio.com/view/subject/s/publi...   
1     https://img1.doubanio.com/view/subject/s/publi...   
2     https://img1.doubanio.com/view/subject/s/publi...   
3     https://img1.doubanio.com/view/subject/s/publi...   
4     https://img2.doubanio.com/view/subject/s/publi...   
...                                                 ...   
8126  https://img9.doubanio.com/view/subject/l/publi...   
8127  https://img9.doubanio.com/view/subject/l/publi...   
8128  https://img9.doubanio.com/view/subject/l/publi...   
8129  https://img9.doubanio.com/view/subject/l/publi...   
8130  https://img9.doubanio.com/view/subject/l/publi...   

                                                READERS  
0     https://www.douban.com/people/scorpio0_0/https...  
1     https://www.douban.com/people/zcj1568/https://...  
2     https://www.douban.com/people/amber_xyxy/https...  
3     https://www.douban.com/people/lostgarden/https...  
4     https://www.douban.com/people/ourdookbook/http...  
...                                                 ...  
8126  ['https://www.douban.com/people/sleepymia/', '...  
8127  ['https://www.douban.com/people/Aterego/', 'ht...  
8128  ['https://www.douban.com/people/doustar/', 'ht...  
8129  ['https://www.douban.com/people/51490972/', 'h...  
8130  ['https://www.douban.com/people/212209628/', '...  

[8131 rows x 12 columns]

In [5]:
#查重，如果有重复的， 保留第一个数据
books = books.drop_duplicates(['BOOK_NAME'], keep='first',ignore_index=True)
books

BOOK_NAME       AUTHOR      PRESS PUBLISHING_YEAR SCORE RATING_NUM  \
0           活着           余华      作家出版社            2012   9.4     588677   
1           文城           余华  北京十月文艺出版社            2021   7.8      11350   
2          白夜行      [日]东野圭吾     南海出版公司            2013   9.1     338400   
3          红楼梦  [清]曹雪芹著、高鹗续    人民文学出版社            1996   9.6     331381   
4        暗夜与黎明     [英]肯·福莱特  江苏凤凰文艺出版社            2021   8.1       2202   
...        ...          ...        ...             ...   ...        ...   
5165      龙头凤尾          马家辉    四川文艺出版社            2016   7.8       4753   
5166        龙朱          沈从文        NaN            2014   8.4        107   
5167      龙王闹海          郑渊洁  湖南少年儿童出版社          1989.7   8.7        733   
5168       龙珠1          鸟山明  中国少年儿童出版社            2005   9.5       1033   
5169  龟岛：斯奈德诗集    [美]加里·斯奈德        NaN            2021   8.6         28   

     PAGE_NUM    PRICE           ISBN  \
0         191   20.00元  9787506365437   
1         348   59.00元  9787530221099   
2         538   39.50元  9787544258609   
3        1606   59.70元  9787020002207   
4         960  118.00元  9787559454935   
...       ...      ...            ...   
5165      336   39.50元  9787541144288   
5166      288     29.8  9787214108586   
5167      158     2.25  9787535804235   
5168      175      6.9  9787500774860   
5169      192    49.00  9787559647252   

                                   CONTENT_INTRODUCTION  \
0     《活着(新版)》讲述了农村人福贵悲惨的人生遭遇。福贵本是个阔少爷，可他嗜赌如命，终于赌光了家...   
1     【编辑推荐】★时隔八年，余华全新长篇重磅归来！◆人生就是自己的往事和他人的序章时代的洪流推着...   
2     东野圭吾万千书迷心中的无冕之王周刊文春推理小说年度BEST10第1名本格推理小说年度BEST...   
3     《红楼梦》是一部百科全书式的长篇小说。以宝黛爱情悲剧为主线，以四大家族的荣辱兴衰为背景，描绘...   
4     《巨人的陨落》作者肯•福莱特重磅新作！全球读者平均2个通宵读完！--------------...   
...                                                 ...   
5165  他们是互不靠近的船舶，却在同一个江湖。 在这样的时局里，每个人都背负着世界的混乱，以及混乱里...   
5166  《含章文库·沈从文集:龙朱》内容简介：作为20世纪中国最优秀文学家之一，沈从文一生创作了大量...   
5167  《龙王闹海》是童话作家郑渊洁所著十二生肖系列童话，该书包括龙珠风波、复活的恐龙、争龙年等多部...   
5168  《龙珠(套装共42册)》是日本著名漫画家鸟山明的得意作品。相传，有七颗龙珠散落在世界的各个角...   
5169  【编辑推荐】 ※垮掉派代表、禅宗诗人、“达摩流浪者”原型斯奈德 ※普利策诗歌奖获奖作品 ※把...   

                                              COVER_URL  \
0     https://img3.doubanio.com/view/subject/s/publi...   
1     https://img1.doubanio.com/view/subject/s/publi...   
2     https://img1.doubanio.com/view/subject/s/publi...   
3     https://img1.doubanio.com/view/subject/s/publi...   
4     https://img2.doubanio.com/view/subject/s/publi...   
...                                                 ...   
5165  https://img9.doubanio.com/view/subject/l/publi...   
5166  https://img9.doubanio.com/view/subject/l/publi...   
5167  https://img9.doubanio.com/view/subject/l/publi...   
5168  https://img9.doubanio.com/view/subject/l/publi...   
5169  https://img9.doubanio.com/view/subject/l/publi...   

                                                READERS  
0     https://www.douban.com/people/scorpio0_0/https...  
1     https://www.douban.com/people/zcj1568/https://...  
2     https://www.douban.com/people/amber_xyxy/https...  
3     https://www.douban.com/people/lostgarden/https...  
4     https://www.douban.com/people/ourdookbook/http...  
...                                                 ...  
5165  ['https://www.douban.com/people/yihuiw/', 'htt...  
5166  ['https://www.douban.com/people/82130690/', 'h...  
5167  ['https://www.douban.com/people/doustar/', 'ht...  
5168  ['https://www.douban.com/people/51490972/', 'h...  
5169  ['https://www.douban.com/people/212209628/', '...  

[5170 rows x 12 columns]

# 数据筛选

In [6]:
#把读者url提出来，然后发现爬取的时候url没有加空格分开
url = books['READERS']
url = pd.DataFrame(url)
url

READERS
0     https://www.douban.com/people/scorpio0_0/https...
1     https://www.douban.com/people/zcj1568/https://...
2     https://www.douban.com/people/amber_xyxy/https...
3     https://www.douban.com/people/lostgarden/https...
4     https://www.douban.com/people/ourdookbook/http...
...                                                 ...
5165  ['https://www.douban.com/people/yihuiw/', 'htt...
5166  ['https://www.douban.com/people/82130690/', 'h...
5167  ['https://www.douban.com/people/doustar/', 'ht...
5168  ['https://www.douban.com/people/51490972/', 'h...
5169  ['https://www.douban.com/people/212209628/', '...

[5170 rows x 1 columns]

In [7]:
#使用正则表达式提取出想要的url，整合到一列表中
i = 0
urls = []
for i in range(5170):
    a = re.findall('https://www.douban.com/people(.*?)http',str(url['READERS'][i]))
    j = 0
    for j in range(len(a)):
        link = 'https://www.douban.com/people' + a[j]
        urls.append(link)
len(urls)
urls

25404

['https://www.douban.com/people/scorpio0_0/',
 'https://www.douban.com/people/yuminshuiqi/',
 'https://www.douban.com/people/103130244/',
 'https://www.douban.com/people/211557160/',
 'https://www.douban.com/people/198990055/',
 'https://www.douban.com/people/zcj1568/',
 'https://www.douban.com/people/153853336/',
 'https://www.douban.com/people/32110737/',
 'https://www.douban.com/people/126747186/',
 'https://www.douban.com/people/154587384/',
 'https://www.douban.com/people/amber_xyxy/',
 'https://www.douban.com/people/simplecarrie/',
 'https://www.douban.com/people/NEARGO/',
 'https://www.douban.com/people/115707608/',
 'https://www.douban.com/people/190948024/',
 'https://www.douban.com/people/lostgarden/',
 'https://www.douban.com/people/moiselletea/',
 'https://www.douban.com/people/Lily1988/',
 'https://www.douban.com/people/219538550/',
 'https://www.douban.com/people/166125914/',
 'https://www.douban.com/people/ourdookbook/',
 'https://www.douban.com/people/225927743/',
 'htt

In [8]:
#删重
links = pd.DataFrame(urls)
links = links.drop_duplicates([0], keep='first',ignore_index=True)
links

0
0           https://www.douban.com/people/scorpio0_0/
1          https://www.douban.com/people/yuminshuiqi/
2            https://www.douban.com/people/103130244/
3            https://www.douban.com/people/211557160/
4            https://www.douban.com/people/198990055/
...                                               ...
20713    https://www.douban.com/people/147972418/', '
20714     https://www.douban.com/people/51490972/', '
20715    https://www.douban.com/people/194241199/', '
20716    https://www.douban.com/people/231883061/', '
20717  https://www.douban.com/people/afghanstain/', '

[20718 rows x 1 columns]

In [9]:
#随机抽取1500条url
links = links.head(10000)
link = links[0].values
link = link.tolist()
links = random.sample(link,1500)
links

['https://www.douban.com/people/juanjuandetudou/',
 'https://www.douban.com/people/89523328/',
 'https://www.douban.com/people/demosthenes/',
 'https://www.douban.com/people/angelcandy92/',
 'https://www.douban.com/people/179616162/',
 'https://www.douban.com/people/184679172/',
 'https://www.douban.com/people/48389706/',
 'https://www.douban.com/people/daneestone/',
 'https://www.douban.com/people/zhangqianhan520/',
 'https://www.douban.com/people/illusionking/',
 'https://www.douban.com/people/cold755/',
 'https://www.douban.com/people/50393226/',
 'https://www.douban.com/people/138643657/',
 'https://www.douban.com/people/91471166/',
 'https://www.douban.com/people/134927227/',
 'https://www.douban.com/people/sunshinevvv/',
 'https://www.douban.com/people/huairentc/',
 'https://www.douban.com/people/leidakong/',
 'https://www.douban.com/people/april317/',
 'https://www.douban.com/people/129222928/',
 'https://www.douban.com/people/205188440/',
 'https://www.douban.com/people/gonemem

In [18]:
#存进数据库里面
sql = """CREATE TABLE READERS_URLS(
    urls TEXT
)"""    
try:
    cursor.execute(sql)
except Exception as e:
    print(e)
    # 发生错误则回滚
    conn.rollback()

(1050, "Table 'readers_urls' already exists")


In [19]:
for link in links:
    sql = """
        INSERT INTO READERS_URLS(urls)
        VALUES(%s)
    """
    data = [(link)]
    try:
        cursor.executemany(sql, data)
        conn.commit()
    except Exception as e:
        print(e)
        conn.rollback()

1

1

1

1

1

...

1

1

1

1

1

In [36]:
#准备再建一个表存处理完毕的数据
sql = """CREATE TABLE BOOKS_DEALED (
                     BOOK_NAME TEXT,
                     AUTHOR TEXT,
                     PRESS TEXT,
                     PUBLISHING_YEAR TEXT,
                     SCORE TEXT,
                     RATING_NUM TEXT,
                     PAGE_NUM TEXT,
                     PRICE TEXT,
                     ISBN TEXT,
                     CONTENT_INTRODUCTION TEXT,
                     COVER_URL TEXT
                     )"""
try:
    cursor.execute(sql)
except Exception as e:
    print(e)
    conn.rollback()
cursor = conn.cursor()

0

In [37]:
book_names = books['BOOK_NAME'].values.tolist()
authors = books['AUTHOR'].values.tolist()
presses = books['PRESS'].values.tolist()
publishing_years = books['PUBLISHING_YEAR'].values.tolist()
scores = books['SCORE'].values.tolist()
rating_nums = books['RATING_NUM'].values.tolist()
page_nums = books['PAGE_NUM'].values.tolist()
prices = books['PRICE'].values.tolist()
ISBNS = books['ISBN'].values.tolist()
content_introductions = books['CONTENT_INTRODUCTION'].values.tolist()
cover_urls = books['COVER_URL'].values.tolist()

In [38]:
#然后发现‘nan can not be used with MySQL’
#没关系，那么我们的数据里面就没有存在缺失值的数据了
for i in range(5170):
    sql = """
        INSERT INTO BOOKS_DEALED(book_name, author, press, publishing_year, score, rating_num,
        page_num, price, ISBN, content_introduction, cover_url)
        VALUES(%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
    """
    data = [(book_names[i], authors[i], presses[i], publishing_years[i], scores[i], rating_nums[i],
            page_nums[i], prices[i], ISBNS[i], content_introductions[i], cover_urls[i])]
    try:
        cursor.executemany(sql, data)
        conn.commit()
    except Exception as e:
        print(e)
        conn.rollback()

1

1

1

1

1

...

1

nan can not be used with MySQL


1

1

nan can not be used with MySQL


# 处理书籍封面

In [3]:
data = pd.read_sql('select * from books_dealed',conn)
data.head(10)

BOOK_NAME          AUTHOR      PRESS PUBLISHING_YEAR SCORE RATING_NUM  \
0        活着              余华      作家出版社            2012   9.4     588677   
1        文城              余华  北京十月文艺出版社            2021   7.8      11350   
2       白夜行         [日]东野圭吾     南海出版公司            2013   9.1     338400   
3       红楼梦     [清]曹雪芹著、高鹗续    人民文学出版社            1996   9.6     331381   
4     暗夜与黎明        [英]肯·福莱特  江苏凤凰文艺出版社            2021   8.1       2202   
5    克拉拉与太阳         [英]石黑一雄    上海译文出版社            2021   8.4       5299   
6  房思琪的初恋乐园             林奕含   北京联合出版公司            2018   9.2     243784   
7       小王子       [法]圣埃克苏佩里    人民文学出版社            2003   9.0     632532   
8      百年孤独  [哥伦比亚]加西亚·马尔克斯     南海出版公司            2011   9.3     331924   
9     追风筝的人      [美]卡勒德·胡赛尼    上海人民出版社            2006   8.9     691306   

  PAGE_NUM    PRICE           ISBN  \
0      191   20.00元  9787506365437   
1      348   59.00元  9787530221099   
2      538   39.50元  9787544258609   
3     1606   59.70元  9787020002207   
4      960  118.00元  9787559454935   
5      392    68.00  9787532786831   
6      272   45.00元  9787559614636   
7       97   22.00元  9787020042494   
8      360   39.50元  9787544253994   
9      362   29.00元  9787208061644   

                                CONTENT_INTRODUCTION  \
0  《活着(新版)》讲述了农村人福贵悲惨的人生遭遇。福贵本是个阔少爷，可他嗜赌如命，终于赌光了家...   
1  【编辑推荐】★时隔八年，余华全新长篇重磅归来！◆人生就是自己的往事和他人的序章时代的洪流推着...   
2  东野圭吾万千书迷心中的无冕之王周刊文春推理小说年度BEST10第1名本格推理小说年度BEST...   
3  《红楼梦》是一部百科全书式的长篇小说。以宝黛爱情悲剧为主线，以四大家族的荣辱兴衰为背景，描绘...   
4  《巨人的陨落》作者肯•福莱特重磅新作！全球读者平均2个通宵读完！--------------...   
5  “太阳总有办法照到我们，不管我们在哪里。”~克拉拉是一个专为陪伴儿童而设计的太阳能人工智能机...   
6  令人心碎却无能为力的真实故事。向死而生的文学绝唱  打动万千读者的年度华语小说。李银河 戴锦...   
7  小王子是一个超凡脱俗的仙童，他住在一颗只比他大一丁点儿的小行星上。陪伴他的是一朵他非常喜爱的...   
8  《百年孤独》是魔幻现实主义文学的代表作，描写了布恩迪亚家族七代人的传奇故事，以及加勒比海沿岸...   
9  12岁的阿富汗富家少爷阿米尔与仆人哈桑情同手足。然而，在一场风筝比赛后，发生了一件悲惨不堪的...   

                                           COVER_URL  
0  https://img3.doubanio.com/view/subject/s/publi...  
1  https://img1.doubanio.com/view/subject/s/publi...  
2  https://img1.doubanio.com/view/subject/s/publi...  
3  https://img1.doubanio.com/view/subject/s/publi...  
4  https://img2.doubanio.com/view/subject/s/publi...  
5  https://img9.doubanio.com/view/subject/s/publi...  
6  https://img3.doubanio.com/view/subject/s/publi...  
7  https://img2.doubanio.com/view/subject/s/publi...  
8  https://img3.doubanio.com/view/subject/s/publi...  
9  https://img3.doubanio.com/view/subject/s/publi...

In [4]:
cover_urls = data['COVER_URL'].values.tolist()
booknames = data['BOOK_NAME'].values.tolist()
len(booknames)
len(cover_urls)

4714

4714

In [45]:
dir="D:\python\Book_Recommendation_System_GUI\cover"
dir

'D:\\python\\Book_Recommendation_System_GUI\\cover'

In [47]:
#下载书籍封面图片
x=0
headers = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/90.0.4430.72 Safari/537.36",
        "Connection":"close"
    }

while x<4714:   
    print(cover_urls[x])
    pic= requests.get(cover_urls[x], headers = headers)
    file_name = str(x) + '.jpg'
    path = dir + file_name
    print(x)
    fp = open(path, 'wb')
    fp.write(pic.content)
    fp.close()
    x=x+1
    print('success')


https://img3.doubanio.com/view/subject/s/public/s29053580.jpg
0


11364

success
https://img1.doubanio.com/view/subject/s/public/s33834057.jpg
1


11799

success
https://img1.doubanio.com/view/subject/s/public/s24514468.jpg
2


...

success
https://img9.doubanio.com/view/subject/l/public/s3245204.jpg
4712


37965

success
https://img9.doubanio.com/view/subject/l/public/s3420949.jpg
4713


32026

success


In [4]:
#此处处理添加进去的是图片在图书管理系统中的相对路径，目的是在程序中显示封面
i = 0
paths = []
for i in range(4714):
    path = 'cover/cover' + str(i) + '.jpg'
    paths.append(path)
paths

['cover/cover0.jpg',
 'cover/cover1.jpg',
 'cover/cover2.jpg',
 'cover/cover3.jpg',
 'cover/cover4.jpg',
 'cover/cover5.jpg',
 'cover/cover6.jpg',
 'cover/cover7.jpg',
 'cover/cover8.jpg',
 'cover/cover9.jpg',
 'cover/cover10.jpg',
 'cover/cover11.jpg',
 'cover/cover12.jpg',
 'cover/cover13.jpg',
 'cover/cover14.jpg',
 'cover/cover15.jpg',
 'cover/cover16.jpg',
 'cover/cover17.jpg',
 'cover/cover18.jpg',
 'cover/cover19.jpg',
 'cover/cover20.jpg',
 'cover/cover21.jpg',
 'cover/cover22.jpg',
 'cover/cover23.jpg',
 'cover/cover24.jpg',
 'cover/cover25.jpg',
 'cover/cover26.jpg',
 'cover/cover27.jpg',
 'cover/cover28.jpg',
 'cover/cover29.jpg',
 'cover/cover30.jpg',
 'cover/cover31.jpg',
 'cover/cover32.jpg',
 'cover/cover33.jpg',
 'cover/cover34.jpg',
 'cover/cover35.jpg',
 'cover/cover36.jpg',
 'cover/cover37.jpg',
 'cover/cover38.jpg',
 'cover/cover39.jpg',
 'cover/cover40.jpg',
 'cover/cover41.jpg',
 'cover/cover42.jpg',
 'cover/cover43.jpg',
 'cover/cover44.jpg',
 'cover/cover45.jpg'

In [ ]:
book_names = data['BOOK_NAME'].values.tolist()
authors = data['AUTHOR'].values.tolist()
presses = data['PRESS'].values.tolist()
publishing_years = data['PUBLISHING_YEAR'].values.tolist()
scores = data['SCORE'].values.tolist()
rating_nums = data['RATING_NUM'].values.tolist()
page_nums = data['PAGE_NUM'].values.tolist()
prices = data['PRICE'].values.tolist()
ISBNS = data['ISBN'].values.tolist()
content_introductions = data['CONTENT_INTRODUCTION'].values.tolist()
cover_urls = books['COVER_URL'].values.tolist()

In [7]:
#存入数据库
sql = """CREATE TABLE BOOK_DEALED (
                     BOOK_NAME TEXT,
                     AUTHOR TEXT,
                     PRESS TEXT,
                     PUBLISHING_YEAR TEXT,
                     SCORE TEXT,
                     RATING_NUM TEXT,
                     PAGE_NUM TEXT,
                     PRICE TEXT,
                     ISBN TEXT,
                     CONTENT_INTRODUCTION TEXT,
                     COVER_URL TEXT,
                     COVERS TEXT
                     )"""
try:
    cursor.execute(sql)
except Exception as e:
    print(e)
    conn.rollback()
cursor = conn.cursor()

(1050, "Table 'book_dealed' already exists")


In [8]:
for i in range(4714):
    sql = """
        INSERT INTO BOOK_DEALED(book_name, author, press, publishing_year, score, rating_num,
        page_num, price, ISBN, content_introduction, cover_url, covers)
        VALUES(%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
    """
    data = [(book_names[i], authors[i], presses[i], publishing_years[i], scores[i], rating_nums[i],
            page_nums[i], prices[i], ISBNS[i], content_introductions[i], cover_urls[i], paths[i])]
    try:       
        cursor.executemany(sql, data)
        conn.commit()
        print('success')
    except Exception as e:
        print(e)
        conn.rollback()

1

success


1

success


1

...

success


1

success


1

success
